In [1]:
import numpy as np
import csv
import numpy.matlib
from operator import itemgetter, attrgetter
from sklearn.model_selection import KFold
from sklearn.metrics import roc_curve, auc
import matplotlib.pyplot as plt

In [2]:
#fp = open('dt_new_and_fda_unique.csv','r')
fp = open('new_dt_from_go_and_db_unique_latest.csv','r')
drugid = []
targetid = []

##1. Reading edge list line by line##
for line in fp:
        line = line.strip()
        tmp = line.split(',')
        drugid.append(tmp[0])
        targetid.append(tmp[1])
fp.close()
##End 1##

drug = np.array(drugid)
target =np.array(targetid)

uni_drugid = np.unique(np.array(drugid))
uni_targetid = np.unique(np.array(targetid))

##creating zero incidence matrix for the graph##

A = np.zeros((uni_targetid.shape[0], uni_drugid.shape[0]))

for i in range(len(drugid)):
                idx1 = np.where(uni_targetid==targetid[i])
                idx2 = np.where(uni_drugid==drugid[i])
                A[idx1,idx2] = 1

nd = uni_drugid.shape[0]
mt = uni_targetid.shape[0]

A_T = np.transpose(A)
no_edges = np.sum(A)
print nd, mt, A.shape, np.sum(A), A_T.shape


6319 3772 (3772, 6319) 26093.0 (6319, 3772)


In [3]:
#NBI calculation for A

Ky = np.diag((1/sum(A))) 
n = A.shape[0]
m = A.shape[1]
#print n, m, Ky.shape
Ky[np.isinf(Ky) | np.isnan(Ky)] = 0
kx = np.transpose(np.sum(A,1))
#print kx.shape
Nx = np.matlib.repmat(1/kx,n,1)
Nx[np.isinf(Nx) | np.isnan(Nx)] = 0
#kx[np.isinf(kx) | np.isnan(kx)] = 0
W = np.transpose(np.dot(A, Ky))
W1 = np.dot(A, W)
W2 = np.multiply(Nx, W1)
print W2.shape
NBIscore = np.dot(W2, A)
print NBIscore.shape

(3772, 3772)
(3772, 6319)


In [4]:
#NBI calculation for A_T

Ky = np.diag((1/sum(A_T)))
n = A_T.shape[0]
m = A_T.shape[1]
#print n, m, Ky.shape
Ky[np.isinf(Ky) | np.isnan(Ky)] = 0
kx = np.transpose(np.sum(A_T,1))
#print kx.shape
Nx = np.matlib.repmat(1/kx,n,1)
Nx[np.isinf(Nx) | np.isnan(Nx)] = 0
#kx[np.isinf(kx) | np.isnan(kx)] = 0
W = np.transpose(np.dot(A_T, Ky))
W1 = np.dot(A_T, W)
W2 = np.multiply(Nx, W1)
NBIscore_T = np.dot(W2, A_T)

In [5]:
##Normalizing NBI scores
NBIscore = np.true_divide(NBIscore, np.max(NBIscore, axis=0))
NBIscore_T = np.true_divide(NBIscore_T, np.max(NBIscore_T, axis=0))

In [7]:
nbi_idx = np.argsort(NBIscore, axis=0)
nbi_idx_T= np.argsort(NBIscore_T, axis=0)

In [8]:
wp = open('predicted_targets_for_all_drugs_using_percent_diff_0.20_.csv','w')
for d in range(nd):
    idx1 = nbi_idx[:,d]
    #idx1 = idx1[::-1]
    idx2 = A[:,d]
    idx3 = idx2[idx1]
    idx4 = np.where(idx3 == 0)[0]
    p_targets_idx = idx1[idx4[-n:]]
    p_targets_idx = p_targets_idx[::-1]
    p_targets = NBIscore[p_targets_idx,d]
    if p_targets[0] == 0.0:
        continue
    else:
        p_diff = np.diff(p_targets)
        th = p_targets[0]*0.20
        th_f = p_targets[0]-th
        f_idx = p_targets_idx[p_targets > th_f]
        f_scores = p_targets[p_targets > th_f]
        f_targets = uni_targetid[f_idx]
        #print p_targets[0], th, th_f, p_targets[p_targets > th_f], p_targets
        for i,t in enumerate(f_targets):
            wp.write(uni_drugid[d] + ',' + t + ',' + str(f_scores[i]) + '\n')

wp.close()